# earthaccess a NASA Earthdata API Client 🌍 in Python

## Overview

**TL;DR**:  *earthaccess* is uses NASA APIs to search, preview and access NASA datasets on-prem and in the cloud with 4 lines of Python.

There are many ways to access NASA datasets, we can use the NASA's Earthdata search portal. We can use DAAC specific websites or tools.
We could even use data.gov! These web portals are great but... they are not designed for programmatic access and reproducible workflows. 
This is extremely important in the age of the cloud and reproducible open science. In this context, **earthaccess** aims to be a simple 
library that can deal with the important parts of the metadata so we can access or download data without having to worry if a given dataset is on-prem or in the cloud.

The core function of auth is to deal with cloud credentials and remote file sessions (fsspec or requests).
essentially, anything that requires you to log in to Earthdata. Most of this will happen behind-the-scenes for you once you have been authenticated.

### NASA EDL and the Auth class

* **Step 1**. We need to open an account with [NASA Eardtada](https://urs.earthdata.nasa.gov/), this credentials will allow us to access NASA datasets.

Once we have our account we can use it with *earthaccess* 

In [1]:
import earthaccess
import geopandas as gpd

auth = earthaccess.login()

In [4]:
auth

## Searching for data using a region of interest

In [5]:
path = "bosque_primavera.json"
# path = "bosque_primavera.kml" 
# path = "bosque_primavera.shp"
gdf = gpd.read_file(path)
geom = earthaccess.load_geometry(path)
gdf

objectid        nombre                                         cat_decret  \
0        61  La Primavera  Zona de Protección Forestal y Refugio de la Fa...   

  cat_manejo  estados                                       municipios  \
0      APFyF  Jalisco  Tala, Zapopan, El Arenal y Tlajomulco de Zuñiga   

                        region  superficie  s_terres  s_marina  ... nom_polig  \
0  Occidente y Pacífico Centro     30500.0   30500.0       0.0  ...             

  cat_uicn fuente instrume vigencia tipo_prop  \
0                                               

                                 globalid   shape_Length    shape_Area  \
0  {A0F7D724-288A-4738-B2EC-01BC557CCF9A}  109128.215997  3.511040e+08   

                                            geometry  
0  POLYGON Z ((-103.49490 20.71534 0.00000, -103....  

[1 rows x 25 columns]

In [7]:
gdf['geometry'].iloc[0].bounds

(-103.686116, 20.544803, -103.454377, 20.726185)

## Search and Access with earthaccess

earthaccess uses NASA's [search API](https://cmr.earthdata.nasa.gov/search/site/docs/search/api.html) to search for data from the different Distributed Archive Centers, the data can be hosted by the DAACs or in AWS, with earthaccess we don't need to think about this because it will handle the authentication for us. For reproducible workflows we just need to use the dataset (or collection as NASA calls them) `concept_id`. 

The `concept_id` of a collection can be found with *earthaccess* or using NASA Earthdata [search portal](https://search.earthdata.nasa.gov/search).


In [ ]:
results = earthaccess.search_data(
    concept_id = ["C2613553260-NSIDC_CPRD", "C2237824918-ORNL_CLOUD", "C1908348134-LPDAAC_ECS", "C2021957657-LPCLOUD", "C2033638023-NSIDC_CPRD"],
    temporal = ("2000", "2023"),
    **geom
)

In [ ]:
m = earthaccess.explore(results, roi=geom)
m

In [ ]:
links = results[500].data_links("external")
print(links)


## Download data (on-prem or cloud)  📡


In [ ]:
%%time
# accessing the data on prem means downloading it if we are in a local environment or "uploading them" if we are in the cloud.
files = earthaccess.download(results[0:2], "./data")
files

## Analysis in place (direct S3 access) ☁️

Same API, just a different origin

In [ ]:
%%time

files = earthaccess.open(results[0:2], "./data")
files

### Related links

**CMR** API documentation: https://cmr.earthaccess.nasa.gov/search/site/docs/search/api.html

**EDL** API documentation: https://urs.earthaccess.nasa.gov/

NASA OpenScapes: https://nasa-openscapes.github.io/earthaccess-cloud-cookbook/

NSIDC: https://nsidc.org

## Subsetting and Reading Icesat-2 Data

In [12]:
import xarray as xr 


# Open HDF5 file
ds = xr.open_dataset('temp/GEDI02_A_2021201084306_O14742_03_T06035_02_003_02_V002.h5')
ds
# Save subset to a new HDF5 file
# with h5py.File('subset_file.h5', 'w') as subset_file:
#     subset_dataset = subset_file.create_dataset('subset_dataset', data=subset_data)


<xarray.Dataset>
Dimensions:                                                              (
                                                                          phony_dim_0: 1,
                                                                          phony_dim_1: 95157,
                                                                          phony_dim_2: 20,
                                                                          phony_dim_3: 101,
                                                                          phony_dim_4: 93122,
                                                                          phony_dim_5: 95351,
                                                                          phony_dim_6: 93166,
                                                                          phony_dim_7: 93125,
                                                                          phony_dim_8: 104099,
                                                                          phony_dim_9: 95624,
                                                                          phony_dim_10: 92983)
Dimensions without coordinates: phony_dim_0, phony_dim_1, phony_dim_2,
                                phony_dim_3, phony_dim_4, phony_dim_5,
                                phony_dim_6, phony_dim_7, phony_dim_8,
                                phony_dim_9, phony_dim_10
Data variables: (12/4384)
    __BEAM0000__ancillary__l2a_alg_count                                 (phony_dim_0) uint8 ...
    __BEAM0000__beam                                                     (phony_dim_1) uint16 ...
    __BEAM0000__channel                                                  (phony_dim_1) uint8 ...
    __BEAM0000__degrade_flag                                             (phony_dim_1) uint8 ...
    __BEAM0000__delta_time                                               (phony_dim_1) datetime64[ns] ...
    __BEAM0000__digital_elevation_model                                  (phony_dim_1) float32 ...
    ...                                                                   ...
    __BEAM1011__selected_mode_flag                                       (phony_dim_10) uint8 ...
    __BEAM1011__sensitivity                                              (phony_dim_10) float32 ...
    __BEAM1011__shot_number                                              (phony_dim_10) uint64 ...
    __BEAM1011__solar_azimuth                                            (phony_dim_10) float32 ...
    __BEAM1011__solar_elevation                                          (phony_dim_10) float32 ...
    __BEAM1011__surface_flag                                             (phony_dim_10) uint8 ...
Attributes:
    short_name:  GEDI_L2A

In [28]:
min_lat = 20.544803
max_lat = 20.726185
min_lon = -103.454377
max_lon = -103.686116

subset_ds = ds.sel(lat_highestreturn=slice(min_lat, max_lat), lon_highestreturn=slice(min_lon, max_lon))
subset_ds

KeyError: "no index found for coordinate 'lat_highestreturn'"

In [22]:
import h5py

def traverse_and_subset_hdf5(group, bounding_box, output_file, indent=""):
    """
    Recursively traverse an HDF5 group, subset datasets, and save to a new HDF5 file.
    """
    for name, item in group.items():
        if isinstance(item, h5py.Group):
            print(f"{indent}Group: {name}")
            traverse_and_subset_hdf5(item, bounding_box, output_file, indent + "  ")
        elif isinstance(item, h5py.Dataset):
            print(f"{indent}Dataset: {name}")
            # Perform subsetting on the dataset
            subset_data = subset_dataset(item, bounding_box)
            
            # Save subset to the output file
            # save_subset_to_file(output_file, f"{name}_subset", subset_data)
        else:
            print(f"{indent}Unknown type: {name}")

def subset_dataset(dataset, bounding_box):
    """
    Subset a dataset based on the specified bounding box.
    """
    # Assuming dataset is 2D, adjust slicing if your data has more dimensions
    min_y, max_y = bounding_box[0]
    min_x, max_x = bounding_box[1]
    # print(dataset.shape, dataset.fields, dataset.attrs, dir(dataset))
    return None

def save_subset_to_file(output_file, dataset_name, subset_data):
    """
    Save a subset to a new HDF5 file.
    """
    with h5py.File(output_file, 'a') as file:
        subset_dataset = file.create_dataset(dataset_name, data=subset_data)

# Open the original HDF5 file
input_file_path = "temp/GEDI02_A_2021201084306_O14742_03_T06035_02_003_02_V002.h5"
with h5py.File(input_file_path, 'r') as input_file:
    # Specify the bounding box
    bounding_box = ((20.544803, 20.726185),  (-103.454377, -103.686116))

    # Create a new HDF5 file for the subset
    output_file_path = 'subset_file.h5'
    with h5py.File(output_file_path, 'w') as output_file:
        # Start traversal and subset operation
        traverse_and_subset_hdf5(input_file, bounding_box, output_file)


Group: BEAM0000
  Group: ancillary
    Dataset: l2a_alg_count
  Dataset: beam
  Dataset: channel
  Dataset: degrade_flag
  Dataset: delta_time
  Dataset: digital_elevation_model
  Dataset: digital_elevation_model_srtm
  Dataset: elev_highestreturn
  Dataset: elev_lowestmode
  Dataset: elevation_bias_flag
  Dataset: elevation_bin0_error
  Dataset: energy_total
  Group: geolocation
    Dataset: elev_highestreturn_a1
    Dataset: elev_highestreturn_a2
    Dataset: elev_highestreturn_a3
    Dataset: elev_highestreturn_a4
    Dataset: elev_highestreturn_a5
    Dataset: elev_highestreturn_a6
    Dataset: elev_lowestmode_a1
    Dataset: elev_lowestmode_a2
    Dataset: elev_lowestmode_a3
    Dataset: elev_lowestmode_a4
    Dataset: elev_lowestmode_a5
    Dataset: elev_lowestmode_a6
    Dataset: elev_lowestreturn_a1
    Dataset: elev_lowestreturn_a2
    Dataset: elev_lowestreturn_a3
    Dataset: elev_lowestreturn_a4
    Dataset: elev_lowestreturn_a5
    Dataset: elev_lowestreturn_a6
    Dataset